# Programmation fonctionnelle

## Fonctions de haut-niveau

Dans un langage fonctionnel, les fonctions sont des citoyens de premier niveau.
La manipulation de fonctions et leur typage sont ainsi facilités.
On peut définir des valeurs et des variables contenant des fonctions.

Le type d'une fonction est `A => B`, où `A` est le type de l'argument et `B` le type de retour de la fonction.

In [19]:
/* /!\ DO NOT FORGET '=', otherwise the return type is 'Unit' */
def incr1(x: Int) = x+1           // argument type is mandatory
def incr2(x: Int): Int = x+1      // return type can be explicited
def incr4 = (x: Int) => x+1       // alternative syntax, the return type is implicit
def incr3: Int => Int = x => x+1  // alternative syntax, note how the argument type is explicited

Rappelons que les fonctions sont des entités comme les autres : une fonction peut prendre une fonction en argument et retourner une fonction.

In [37]:
def add_cste(c: Int) = (x: Int) => x+c
def apply(f: Int => Int, x: Int) = f(x)
def compose(f: Int => Int, g: Int => Int) = (x: Int) => f(g(x))

## Fonctions curryfiées

Considérons la fonction `add_cste` ci-dessus.
Elle prend un entier en argument, et retourne une fonction de type `Int => Int`.
Le type de `add_cste` est donc `Int => (Int => Int)`.
Soient `a` et `b` deux valeurs (ou variables, peu importe) de type `Int`.
`add_cste(a)` est de type `Int => Int`, donc on peut l'appliquer à `b`, ce qui donne un entier `add_cste(a)(b)`.
Remarquez que cet entier n'est autre que `a+b`.
On pourrait implémenter la même opération avec la fonction `def add(x: Int, y: Int) = a+b`, de type `(Int, Int) => Int`.

On appelle `add_cste` une fonction _curryfiée_ : plutôt que d'avoir plusieurs arguments, elle a un seul argument et renvoie une fonction des autres arguments.
Le passage d'une fonction non-curryfiée (comme `add`) à une fonction curryfiée (comme `add_cste`) s'appelle la _curryfication_ ("_currying_" en anglais).
L'opération inverse s'appelle la _décurryfication_.  
La curryfication permet d'appliquer _partiellement_ des fonctions.
Par exemple, on peut définir une fonction qui incrémente un entier comme `def incr = add_cste(1)`.
Similairement, une fonction de décrémentation est obtenue comme `def decr = add_cste(-1)`.  
Remarquez comme la curryfication permet de partager le code de `incr` et `decr` (même si cela paraît futile pour cet exemple).

**NB :** comme la curryfication permet d'appliquer aux différents arguments un par un, l'opération `=>` sur les types est _associative_ à droite, ce qui permet d'éliminer des parenthèses.
Le type `Int => (Int => Int)` peut se noter `Int => Int => Int`.
Attention, il est différent du type `(Int => Int) => Int`, dont l'argument est une fonction et le type de retour est `Int`.

# Exercice : Entiers de Church

Les entiers de Church sont un encodage des entiers naturels dans le lambda-calcul, qui est un modèle théorique des langages de programmation fonctionnels.  
L'entier `n` est codée comme une fonction qui prend deux arguments `f` et `x` et renvoie `f^n(x)`, c'est-à-dire `f` composée `n` fois à elle-même appliquée à `x`.  
On rappelle que `f^0(x) = x` et `f^1(x) = f`.
Pour simplifier, on considère que `x` est de type `Int` : `f` est donc de type `Int => Int`.
Un entier de Church est donc de type `(Int => Int) => Int => Int`, type que l'on notera `ChurchNumber` pour raccourcir.

On cherche à implémenter une fonction `church` de type `Int => (Int => Int) => Int => Int` qui à un entier naturel `n` associe son entier de Church.
1. Implémentez l'entier de Church représentant 0.
2. Implémentez la fonction `succ`, de type `ChurchNumber => ChurchNumber`, qui à un entier de Church `n` associe l'entier de Church correspondant à `n+1`.
3. Implémentez la fonction `church`, qui à un `Int` associe le `ChurchNumber` correspondant. Cette fonction peut être définie récursivement à partir de `zero` et de `succ`.
4. Implémentez l'opération `add` sur les entiers de Church.
5. Implémentez l'opération `multiply` sur les entiers de Church.

In [1]:
// a useful typedef
type ChurchNumber = (Int=>Int) => Int => Int

def zero(f: Int=>Int)(x: Int) = /* TODO */
def succ(n: ChurchNumber): ChurchNumber = /* TODO */
def church: Int => ChurchNumber = /* TODO */

def add(n: ChurchNumber)(p: ChurchNumber): ChurchNumber = /* TODO */
    
def multiply(n: ChurchNumber)(p: ChurchNumber): ChurchNumber = /* TODO */
    
// tests
val incr = (x:Int) => x+1
def test(n: ChurchNumber) = n(incr)(0)
println(test(church(0))) // 0
println(test(church(5))) // 5
println(test(add(church(2))(church(5)))) // 7
println(test(multiply(church(2))(church(5)))) // 10

0
5
7
10


# Exercice : Implémenter des ensembles avec des fonctions

On rappelle qu'un ensemble `E` peut être vu comme une fonction booléenne, sa _fonction caractéristique_.
On identifie ici un ensemble avec sa fonction caractéristique.
`E(x)` renvoie `true` si et seulement si `x` appartient à `E`.
Implémentez les opérations `union`, `intersection`, `complement`, `difference`, `symmetric_difference` sur les fonctions charactéristiques.
Implémentez aussi une fonction qui associe à une liste d'entiers la fonction caractéristique correspondante.

In [23]:
type IntSet = Int => Boolean

// printSet(S) actually prints the set (S inter [0..9])
def printSet(S: IntSet) = 
    for (var i = 0; i < 10; ++i) {
        if (S(i)) {
            print(i, ",");
        }
    }
    println("")

def insert: IntSet => Int => IntSet = /* TODO */
def erase: IntSet => Int => IntSet = /* TODO */
def union: IntSet => IntSet => IntSet = /* TODO */
def intersection: IntSet => IntSet => IntSet = /* TODO */
def complement: IntSet => IntSet = /* TODO */
def difference: IntSet => IntSet => IntSet = /* TODO */
def symmetric_difference: IntSet => IntSet => IntSet = /* TODO */

def fromSet: Set[Int] => IntSet = /* TODO */

val S1 = List(1, 2, 3)
val S2 = List(2, 4, 6)

printSet(union(S1)(S2))                 // 1,2,3,4,6
printSet(intersection(S1)(S2))          // 2
printSet(complement(S1))                // 0,4,5,6,7,8,9
printSet(difference(S2)(S1))            // 4,6
printSet(symmetric_difference(S1)(S2))  // 1,3,4,6

Name: Compile Error
Message: <console>:3: error: illegal start of simple pattern
           for (var i = 0; i <= 10; ++i) {
                ^
<console>:3: error: '<-' expected but ';' found.
           for (var i = 0; i <= 10; ++i) {
                         ^
<console>:3: error: '<-' expected but ';' found.
           for (var i = 0; i <= 10; ++i) {
                                  ^
<console>:3: error: illegal start of simple pattern
           for (var i = 0; i <= 10; ++i) {
                                       ^
StackTrace: 